In [1]:
HPA_OBSERVATION_SPACE_ELEMS = [
    "buf_size_idx",                      # Index form of the buffer size value [0, 63]
    "observation.cache_used_pages_ratio",    # Buffer cache fill rate in [0., 1.]
]
ext_threshold=0.99

BFR_OBSERVATION_SPACE_ELEMS = [
    "observation.cache_used_pages_ratio"
]

In [2]:
import reward as rw
import datasource.adbms_live as ds

#from policy_sb3 import SB3Policy
from policy_baselines import TopDownPolicy, BufFillingRatePolicy

from gym_env import VSEnv, VSMonitor
from agent import VSAgent, SB3VSAgent


ACTION_MINMAX = (-1,1)  # The Min and Max action values. Arms count and the position of the "STAY" arm are depending on it.

reward = rw.ADBMSBufferCacheRewardContinousV3E(action_minmax=(-1,1)) 

# TODO: Load model and scaler if any

# DataSet with states from a Live DB (by default db.local) 
ds_states_test = ds.ADBMSBufferCacheStates(dbhost="192.168.0.143") # db.local TUN06=192.168.0.143

TEST_EPISODES_COUNT = 1  #-2    # If <0, abs(EPISODES_COUNT) is a multiple of workloads count 
TEST_STEPS_PER_EPISODE = 300 # -1 # If <0, abs(STEPS_PER_EPISODE) is a multiple of buffer values count 

ds_states_test.prepareContext(BFR_OBSERVATION_SPACE_ELEMS, normalize=False, with_scaler=None) 

# Environement for test with VSMonitor Wrapper. 
env_test = VSMonitor(VSEnv(ds_states_test, reward=reward, notify_react=False, max_steps_per_episode=TEST_STEPS_PER_EPISODE, verbose=1))
#stb3_agent.policy.deterministic = False # Choosing True seems to work badly
#stb3_agent.predict(env_test, episodes_max=TEST_EPISODES_COUNT)

#policy = TopDownPolicy(reward.actions, ctx=ds_states_test.contextElems())
policy = BufFillingRatePolicy(reward.actions, ctx=ds_states_test.contextElems())
agent = VSAgent(policy)
agent.predict(env_test, episodes_max=TEST_EPISODES_COUNT)
env_test.close()


2024-08-22 12:52:49.351899: I tensorflow/core/util/port.cc:110] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-08-22 12:52:49.386106: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


** BUFFER VALUES: [134217728, 268435456, 402653184, 536870912, 671088640, 805306368, 939524096, 1073741824, 1207959552, 1342177280, 1476395008, 1610612736, 1744830464, 1879048192, 2013265920, 2147483648, 2281701376, 2415919104, 2550136832, 2684354560, 2818572288, 2952790016, 3087007744, 3221225472, 3355443200, 3489660928, 3623878656, 3758096384, 3892314112, 4026531840, 4160749568, 4294967296, 4429185024, 4563402752, 4697620480, 4831838208, 4966055936, 5100273664, 5234491392, 5368709120, 5502926848, 5637144576, 5771362304, 5905580032, 6039797760, 6174015488, 6308233216, 6442450944, 6576668672, 6710886400, 6845104128, 6979321856, 7113539584, 7247757312, 7381975040, 7516192768, 7650410496, 7784628224, 7918845952, 8053063680, 8187281408, 8321499136, 8455716864, 8589934592] 64  values
DB USAGE on reset:  {'qps': 17.0, 'threads_connected': 2, 'created_tmp_disk_tables_per_sec': 0.0, 'db_size': {'Schema': 'adbms', 'Engine': 'InnoDB', 'TableSizeMB': 292.14, 'IndexSizeMB': 30.19}}
Prepare Contex